### <font size=5px color="red">✦ *Google Colab 突破90分钟自动断开:</font>
<p><font size=3px > 每60分钟自动运行代码以刷新90分钟断开限制. 打开 developer-settings (在你的浏览器) 快速健 Ctrl+Shift+I 然后按console 输入以下代码 Enter. ( mac 按 Option+Command+I)</p><b>复制以下隐藏代码粉贴在浏览器console！！不要关闭浏览器以免失效</b>

**加粗文字**
```
function ConnectButton(){
    console.log("Connect pushed");
    document.querySelector("#top-toolbar > colab-connect-button").shadowRoot.querySelector("#connect").click()
}
setInterval(ConnectButton,60000);
```

**如果需要停止则将以下内容粘贴在console**
```
clearInterval(intervalId) # intervalId换成具体的数字
```

# **安装FFMPEG**

In [ ]:
!apt-get install ffmpeg

# **挂载`google drive`**

In [ ]:
from google.colab import drive

drive.mount('/content/drive')

查看`GPU`型号

In [ ]:
print("============查看GPU信息================")
# 查看GPU信息
!/opt/bin/nvidia-smi
print("==============查看pytorch版本==============")
# 查看pytorch版本
import torch
print(torch.__version__)
print("============查看虚拟机硬盘容量================")
# 查看虚拟机硬盘容量
!df -lh
print("============查看cpu配置================")
# 查看cpu配置
!cat /proc/cpuinfo | grep model\ name
print("=============查看内存容量===============")
# 查看内存容量
!cat /proc/meminfo | grep MemTotal

# **安装字体**

In [ ]:
import shutil
import os
import concurrent.futures
#import threading

def copy_fonts(root_folder, target_folder):
    # 更改文件系统权限，使其可写
    # !sudo mount -o remount,rw /

    with concurrent.futures.ThreadPoolExecutor() as executor:
        futures = []
        for root, dirs, files in os.walk(root_folder):
            for file in files:
                if file.lower().endswith(('.ttf', '.ttc', '.otf', '.TTF')):
                    font_path_src = os.path.join(root, file)
                    font_path_dst = os.path.join(target_folder, file)
                    futures.append(executor.submit(_copy_font, font_path_src, font_path_dst))
                    #_copy_font(font_path_src, font_path_dst)

        concurrent.futures.wait(futures)  # 等待所有线程完成

    # 恢复文件系统权限为只读
    # !sudo mount -o remount,ro /

def _copy_font(font_path_src, font_path_dst):
    #thread_id = threading.get_ident()  # 获取当前线程的标识
    #print(f"id={thread_id}")
    if not os.path.exists(font_path_dst):
        shutil.copy(font_path_src, font_path_dst)
        print(f"已安装字体: {os.path.basename(font_path_src)}")

# 替换为实际的根目录和目标目录
root_directory = '/content/drive/MyDrive/ownbackup/我的windows字体'
target_directory = '/usr/share/fonts/truetype/'

# 复制字体文件
copy_fonts(root_directory, target_directory)

# 更新字体缓存
!fc-cache -vf

# **字幕转换** 将字幕转换为`UTF-8`

In [ ]:
import os
import chardet
import codecs

def convert_to_utf8(file_path):
    # 读取文件内容并检测编码
    with open(file_path, 'rb') as file:
        raw_data = file.read()
        result = chardet.detect(raw_data)
        encoding = result['encoding']

    # 如果检测到的编码不是UTF-8，进行转码
    if encoding and encoding.lower() != 'utf-8':
        with codecs.open(file_path, 'r', encoding, errors='ignore') as file:
            content = file.read()

        with codecs.open(file_path, 'w', 'utf-8') as file:
            file.write(content)

        print(f"已将文件 {file_path} 转码为 UTF-8")
    else:
        print(f"文件 {file_path} 已经是 UTF-8 编码")

def batch_convert(folder_path):
    # 遍历目标文件夹下的所有文件
    for root, dirs, files in os.walk(folder_path):
        for file in files:
            file_path = os.path.join(root, file)
            # 检查文件是否是字幕文件，你可以根据需要添加更多的字幕文件扩展名
            if file.lower().endswith(('.srt', '.ass', '.sub')):
                convert_to_utf8(file_path)

if __name__ == "__main__":
    target_folder = "/content/drive/MyDrive/ownbackup/togd"
    batch_convert(target_folder)


# **检测字幕文件是否缺失字体**

In [ ]:
import os
import re

def extract_fonts_from_ass(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        content = file.read()

    font_pattern = re.compile(r'Style:\s*[^,]+,([^,]+),[^,]+,[^,]+,[^,]+,[^,]+,[^,]+,[^,]+', re.IGNORECASE)
    fonts = set(font_pattern.findall(content))

    return fonts

def is_font_installed(font_name):
    for root, dirs, files in os.walk('/usr/share/fonts/'):
        for file in files:
            if font_name.lower() in file.lower():
                return True
    return False

def find_missing_fonts(target_directory):
    missing_fonts = set()

    for root, dirs, files in os.walk(target_directory):
        for file in files:
            if file.endswith('.ass'):
                file_path = os.path.join(root, file)
                subtitle_fonts = extract_fonts_from_ass(file_path)

                for font in subtitle_fonts:
                    if not is_font_installed(font):
                        #print(f"{file}缺失字体:{font}")
                        missing_fonts.add(font)

    return missing_fonts

def main():
    target_directory = '/content/drive/MyDrive/ownbackup/togd'
    missing_fonts = find_missing_fonts(target_directory)

    if missing_fonts:
        print("缺失的字体：")
        print(', '.join(missing_fonts))
    else:
        print("所有字幕文件中的字体都存在。")

if __name__ == "__main__":
    main()


# **修改并运行`ffmpeg`命令**



In [ ]:
import os
import subprocess

# 指定多个输入文件夹
input_folders = [
    "/content/drive/MyDrive/ownbackup/togd",
    # Add more input folders if needed
]

# 定义字幕文件后缀列表
subtitle_suffixes = [".SOSG", ".SC", ".sc_w2jmoe", ".sc" , ".chs" , ""]

for input_folder in input_folders:
    #output_folder = os.path.join(input_folder, "output")

    #if not os.path.exists(output_folder):
    #    os.makedirs(output_folder)

    for root, dirs, files in os.walk(input_folder):
        for filename in files:
            if filename.endswith(".mkv"):
                subtitle_path = None
                check = 0
                # 遍历字幕文件后缀列表
                for suffix in subtitle_suffixes:
                    subtitle_file = os.path.splitext(filename)[0] + f"{suffix}.ass"
                    subtitle_path = os.path.join(root, subtitle_file)
                    if os.path.exists(subtitle_path):
                        check = 1
                        print(f"Found subtitle file: {subtitle_file}")
                        break  # 找到字幕文件后立即结束循环

                if check != 0:
                    # 根据视频文件的位置构建输出文件夹
                    output_folder = os.path.join(os.path.dirname(os.path.join(root, filename)), "output")
                    if not os.path.exists(output_folder):
                        os.makedirs(output_folder)
                    output_filename = os.path.join(output_folder, f"{os.path.splitext(filename)[0]}_with_subtitles.mkv")
                    if os.path.exists(output_filename):
                      print(f"存在文件{output_filename}")
                      pass
                    else:
                      # 获取原始视频的视频码率
                      # ffprobe_command = f'ffprobe -show_entries format=bit_rate -of default=noprint_wrappers=1:nokey=1 "{os.path.join(root, filename)}"'
                      # original_bitrate = subprocess.check_output(ffprobe_command, shell=True, text=True).strip()
                      # print(f"original_bit= {original_bitrate}")
                      # 构建 ffmpeg 命令，源码率
                      # cmd = f'ffmpeg -hwaccel nvdec -n -i "{os.path.join(root, filename)}" -c:v hevc_nvenc -b:v {original_bitrate} -preset fast -vf "ass=\'{subtitle_path}\'" -c:a copy "{output_filename}"'
                      # 压制内封字幕时需要进入当前文件目录，因为内封字幕不能指定路径，只能是文件名。无损
                      # cmd = f'ffmpeg -i "{video_filename}" -map 0:v:0 -map 0:a:0 -vf "subtitles=\'{video_filename}\':si=0" -c:v hevc_nvenc -qp 0 -preset p7 "{output_filename}"'
                      # 构建 ffmpeg 命令，默认码率
                      #cmd = f'ffmpeg -hwaccel nvdec -n -i "{os.path.join(root, filename)}" -c:v hevc_nvenc -preset fast -vf "ass=\'{subtitle_path}\'" -c:a copy "{output_filename}"'
                      # 构建 ffmpeg 命令，无损码率+最高画质 p7
                      cmd = f'ffmpeg -hwaccel nvdec -n -i "{os.path.join(root, filename)}" -c:v hevc_nvenc -qp 0 -preset p7 -vf "ass=\'{subtitle_path}\'" -c:a copy "{output_filename}"'
                      process = subprocess.Popen(cmd, shell=True, stdout=subprocess.PIPE, stderr=subprocess.STDOUT, text=True)

                      # 实时输出ffmpeg的运行情况
                      for line in process.stdout:
                          print(line.strip())
                      print(f"Sucess for {subtitle_path}")
                      #print(f"output:{output_folder}")
                else:
                  print(f"Fail for {filename}")


单文件

In [ ]:
import subprocess

input_file = '/content/drive/MyDrive/ownbackup/[VCB-Studio] Himouto! Umaru-chan R [Ma10p_1080p]/[VCB-Studio] Himouto! Umaru-chan R [01][Ma10p_1080p][x265_flac].mkv'
ass_file = '/content/drive/MyDrive/ownbackup/[VCB-Studio] Himouto! Umaru-chan R [Ma10p_1080p]/[VCB-Studio] Himouto! Umaru-chan [01][Ma10p_1080p][x265_2flac].Kamigami-SC.ass'
output_file = '/content/drive/MyDrive/ownbackup/[VCB-Studio] Himouto! Umaru-chan R [Ma10p_1080p]/1.mkv'

ffmpeg_command = f'ffmpeg -y -i "{input_file}" -c:v hevc_nvenc -preset slow -vf "ass=\'{ass_file}\'" -c:a copy "{output_file}"'
#ffmpeg_command = f'ffmpeg -y -i "{input_file}" -c:v libx265 -preset slow -vf "ass=\'{ass_file}\'" -c:a copy "{output_file}"'
#ffmpeg_command = f'ffmpeg -y -i "{input_file}" -c:v hevc_nvenc -preset slow -vf "subtitles=\'{ass_file}\'" -c:a copy -scodec mov_text "{output_file}"'

# 使用 Popen 以便能够读取 stderr 输出
process = subprocess.Popen(ffmpeg_command, shell=True, stderr=subprocess.PIPE)

# 读取并打印输出
while True:
    line = process.stderr.readline().decode()
    if not line:
        break
    print(line.strip())
